In [2]:
import pandas as pd
import numpy as np
import csv
import zipfile

from matplotlib import pyplot as plt
%matplotlib inline
filepath = "../resources/food.csv.zip"
zf = zipfile.ZipFile(filepath)
food = pd.read_csv(zf.open('food.csv'), parse_dates=True, dtype=object, delimiter="\t", quoting=csv.QUOTE_NONE, encoding='utf-8')
pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows',10)
food

code                                                url  \
0       0000000003087  http://world-en.openfoodfacts.org/product/0000...   
1       0000000024600  http://world-en.openfoodfacts.org/product/0000...   
2       0000000027083  http://world-en.openfoodfacts.org/product/0000...   
3       0000000027205  http://world-en.openfoodfacts.org/product/0000...   
4       0000000036252  http://world-en.openfoodfacts.org/product/0000...   
...               ...                                                ...   
106453       99111250  http://world-en.openfoodfacts.org/product/9911...   
106454           9918  http://world-en.openfoodfacts.org/product/9918...   
106455  9935010000003  http://world-en.openfoodfacts.org/product/9935...   
106456       99410148  http://world-en.openfoodfacts.org/product/9941...   
106457  9970229501521  http://world-en.openfoodfacts.org/product/9970...   

                           creator   created_t      created_datetime  \
0       openfoodfacts-contributors  1474103866  2016-09-17T09:17:46Z   
1                  date-limite-app  1434530704  2015-06-17T08:45:04Z   
2                  canieatthis-app  1472223782  2016-08-26T15:03:02Z   
3                          tacinte  1458238630  2016-03-17T18:17:10Z   
4                          tacinte  1422221701  2015-01-25T21:35:01Z   
...                            ...         ...                   ...   
106453                    balooval  1367163039  2013-04-28T15:30:39Z   
106454                  woshilapin  1430167954  2015-04-27T20:52:34Z   
106455                    sebleouf  1446293229  2015-10-31T12:07:09Z   
106456             date-limite-app  1463936572  2016-05-22T17:02:52Z   
106457                      tomato  1422099377  2015-01-24T11:36:17Z   

       last_modified_t last_modified_datetime  \
0           1474103893   2016-09-17T09:18:13Z   
1           1434535914   2015-06-17T10:11:54Z   
2           1472223782   2016-08-26T15:03:02Z   
3           1458238638   2016-03-17T18:17:18Z   
4           1422221855   2015-01-25T21:37:35Z   
...                ...                    ...   
106453      1371690556   2013-06-20T01:09:16Z   
106454      1430167992   2015-04-27T20:53:12Z   
106455      1446376839   2015-11-01T11:20:39Z   
106456      1463941614   2016-05-22T18:26:54Z   
106457      1461433284   2016-04-23T17:41:24Z   

                               product_name                     generic_name  \
0                        Farine de blé noir                              NaN   
1                             Filet de bœuf                              NaN   
2       Marks % Spencer 2 Blueberry Muffins                              NaN   
3                                       NaN                              NaN   
4                            Lion Peanut x2                              NaN   
...                                     ...                              ...   
106453                   Thé vert Earl grey                thé bio équitable   
106454           Cheese cake thé vert, yuzu                              NaN   
106455                       Rillette d'oie                              NaN   
106456                                  NaN                              NaN   
106457                              乐吧泡菜味薯片  Leba pickle flavor potato chips   

       quantity     packaging packaging_tags                 brands  \
0           1kg           NaN            NaN        Ferme t'y R'nao   
1       2.46 kg     plastique      plastique                    NaN   
2          230g           NaN            NaN                    NaN   
3           NaN           NaN            NaN                    NaN   
4           NaN           NaN            NaN                    NaN   
...         ...           ...            ...                    ...   
106453     50 g  boîte,carton   boite,carton                Lobodis   
106454      NaN           NaN            NaN                    NaN   
106455    180 g     Pot,Verre      pot,verre  Sans

In [3]:
def no_null_objects(data, columns=None):
    if columns is None:
        columns = data.columns
    return data[np.logical_not(np.any(data[columns].isnull().values, axis=1))]

In [4]:
def splitDataFrameList(df, target_column, separator):
    def splitListToRows(row, row_accumulator, target_column, separator):
        split_row = row[target_column].split(separator)
        for s in split_row:
            new_row = row.to_dict()
            new_row[target_column] = s
            row_accumulator.append(new_row)
    new_rows = []
    df.apply(splitListToRows,axis=1,args = (new_rows,target_column,separator))
    new_df = pd.DataFrame(new_rows)
    return new_df

In [5]:
food_countries = splitDataFrameList(no_null_objects(food, ["countries_en", 'additives_n', 'allergens']), "countries_en", ",")
countries = food_countries["countries_en"]
countries_temp = (countries.unique())
countries_temp

array(['France', 'United Kingdom', 'Spain', 'United States', 'Belgium',
       'Netherlands', 'Ireland', 'Canada', 'Australia', 'Czech Republic',
       'Indonesia', 'Denmark', 'Norway', 'Sweden', 'Germany', 'Lebanon',
       'Finland', 'Portugal', 'Italy', 'Switzerland', 'fr:Angleterre',
       'French Polynesia', 'Romania', 'de:Scotland', 'European Union',
       'Slovenia', 'Allemagne', 'Poland', 'Peru', 'Morocco', 'Luxembourg',
       'Guadeloupe', 'French Guiana', 'Gabon', 'Tunisia', 'Martinique',
       'Réunion', 'New Caledonia', 'Saint Pierre and Miquelon', 'Greece',
       'Austria', 'Hungary', 'Russia', 'India', 'Armenia', 'China',
       'Saudi Arabia', 'Japan', 'Cyprus', 'Scotland', 'Estonia', 'Malta',
       'New Zealand', 'South Africa', 'United Arab Emirates', 'Mexico',
       'Serbia', 'Bulgaria', 'fr:Marseille-6', 'Brazil', 'Montenegro',
       'Algeria', 'Andorra', 'Iraq', 'Singapore', 'Thailand'], dtype=object)

In [6]:
# outliers 
#food_fat_outlier =food[food['fat_100g'].astype(float) + food['protiens_100g'].astype(float) + food['fat_100g'].astype(float) > 100]
#food_fat_outlier

food_carbohydrates_outlier =food[food['carbohydrates_100g'].astype(float) > 100]
food_carbohydrates_outlier

food_fat_outlier =food[food['fat_100g'].astype(float) > 100]
food_fat_outlier

#food_sugars_outlier =food[food['proteins_100g'].astype(float) > 100]
#food_sugars_outlier




code                                                url  \
94265  8005305900255  http://world-en.openfoodfacts.org/product/8005...   

       creator   created_t      created_datetime last_modified_t  \
94265  mathias  1430147873  2015-04-27T15:17:53Z      1433016494   

      last_modified_datetime               product_name generic_name quantity  \
94265   2015-05-30T20:08:14Z  Ekstra Jomfru Olivenolie           NaN       1L   

      packaging packaging_tags     brands brands_tags categories  \
94265       NaN            NaN  Santagata   santagata        NaN   

      categories_tags categories_en origins origins_tags manufacturing_places  \
94265             NaN           NaN  Europe       europe                Italy   

      manufacturing_places_tags labels labels_tags labels_en emb_codes  \
94265                     italy    NaN         NaN       NaN       NaN   

      emb_codes_tags first_packaging_code_geo cities cities_tags  \
94265            NaN                      NaN    NaN         NaN   

      purchase_places   stores countries countries_tags countries_en  \
94265             NaN  Kvickly   Denmark     en:denmark      Denmark   

      ingredients_text allergens allergens_en traces traces_tags traces_en  \
94265              NaN       NaN          NaN    NaN         NaN       NaN   

      serving_size no_nutriments additives_n additives additives_tags  \
94265          NaN           NaN         NaN       NaN            NaN   

      additives_en ingredients_from_palm_oil_n ingredients_from_palm_oil  \
94265          NaN                         NaN                       NaN   

      ingredients_from_palm_oil_tags ingredients_that_may_be_from_palm_oil_n  \
94265                            NaN                                     NaN   

      ingredients_that_may_be_from_palm_oil  \
94265                                   NaN   

      ingredients_that_may_be_from_palm_oil_tags nutrition_grade_uk  \
94265                                        NaN                NaN   

      nutrition_grade_fr pnns_groups_1 pnns_groups_2  \
94265                  e       unknown       unknown   

                                                  states  \
94265  en:to-be-completed, en:nutrition-facts-complet...   

                                             states_tags  \
94265  en:to-be-completed,en:nutrition-facts-complete...   

                                               states_en main_category  \
94265  To be completed,Nutrition facts completed,Ingr...           NaN   

      main_category_en                                          image_url  \
94265              NaN  http://en.openfoodfacts.org/images/products/80...   

                                         image_small_url energy_100g  \
94265  http://en.openfoodfacts.org/images/products/80...        3737   

      energy-from-fat_100g fat_100g saturated-fat_100g -butyric-acid_100g  \
94265                  NaN      101                 15                NaN   

      -caproic-acid_100g -caprylic-acid_100g -capric-acid_100g  \
94265                NaN                 NaN               NaN   

      -lauric-acid_100g -myristic-acid_100g -palmitic-acid_100g  \
94265               NaN                 NaN                 NaN   

      -stearic-acid_100g -arachidic-acid_100g -behenic-acid_100g  \
94265                NaN                  NaN                NaN   

      -lignoceric-acid_100g -cerotic-acid_100g -montanic-acid_100g  \
94265                   NaN                NaN                 NaN   

      -melissic-acid_100g monounsaturated-fat_100g polyunsaturated-fat_100g  \
94265                 NaN                      NaN                      NaN   

      omega-3-fat_100g -alpha-linolenic-acid_100g -eicosapentaenoic-acid_100g  \
94265              NaN                        NaN                         NaN   

      -docosahexaenoic-acid_100g omega-6-fat_100g -linoleic-acid_100g  \
94265                        NaN              NaN                 NaN   

    

In [7]:
food_countries['allergens'] = food_countries['allergens'].str.split(',').apply(len)
food_countries['additives_n'] = food_countries['additives_n'].astype(int)
food_countries
#countries_final = np.ndarray.sort(countries_temp)
#countries_final

-alpha-linolenic-acid_100g -arachidic-acid_100g -arachidonic-acid_100g  \
0                            NaN                  NaN                    NaN   
1                            NaN                  NaN                    NaN   
2                            NaN                  NaN                    NaN   
3                            NaN                  NaN                    NaN   
4                            NaN                  NaN                    NaN   
...                          ...                  ...                    ...   
23881                        NaN                  NaN                    NaN   
23882                        NaN                  NaN                    NaN   
23883                        NaN                  NaN                    NaN   
23884                        NaN                  NaN                    NaN   
23885                        NaN                  NaN                    NaN   

       -behenic-acid_100g  -butyric-acid_100g  -capric-acid_100g  \
0                     NaN                 NaN                NaN   
1                     NaN                 NaN                NaN   
2                     NaN                 NaN                NaN   
3                     NaN                 NaN                NaN   
4                     NaN                 NaN                NaN   
...                   ...                 ...                ...   
23881                 NaN                 NaN                NaN   
23882                 NaN                 NaN                NaN   
23883                 NaN                 NaN                NaN   
23884                 NaN                 NaN                NaN   
23885                 NaN                 NaN                NaN   

       -caproic-acid_100g  -caprylic-acid_100g  -cerotic-acid_100g  \
0                     NaN                  NaN                 NaN   
1                     NaN                  NaN                 NaN   
2                     NaN                  NaN                 NaN   
3                     NaN                  NaN                 NaN   
4                     NaN                  NaN                 NaN   
...                   ...                  ...                 ...   
23881                 NaN                  NaN                 NaN   
23882                 NaN                  NaN                 NaN   
23883                 NaN                  NaN                 NaN   
23884                 NaN                  NaN                 NaN   
23885                 NaN                  NaN                 NaN   

       -dihomo-gamma-linolenic-acid_100g -docosahexaenoic-acid_100g  \
0                                    NaN                        NaN   
1                                    NaN                        NaN   
2                                    NaN                        NaN   
3                                    NaN                        NaN   
4                                    NaN                        NaN   
...                                  ...                        ...   
23881                                NaN                        NaN   
23882                                NaN                        NaN   
23883                                NaN                        NaN   
23884                                NaN                        NaN   
23885                                NaN                        NaN   

      -eicosapentaenoic-acid_100g  -elaidic-acid_100g  -erucic-acid_100g  \
0                             NaN                 NaN                NaN   
1                             NaN                 NaN                NaN   
2                             NaN                 NaN                NaN   
3                             NaN                 NaN                NaN   
4                             NaN                 NaN                NaN   
...                           ...                 ...                ...   
23

In [8]:
#food_countries.groupby('countries_en', as_index=False)['allergens'].mean()
final_data = food_countries.groupby('countries_en', as_index=False)['allergens','additives_n'].mean()

pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows',100)

plot_data = final_data.sort(['allergens', 'additives_n'], ascending=[0, 0])

plot_data

d:\Users\Odin\Anaconda3\lib\site-packages\ipykernel\__main__.py:7: FutureWarning: sort(columns=....) is deprecated, use sort_values(by=.....)


countries_en  allergens  additives_n
37                    Morocco   7.000000     4.000000
53                   Slovenia   7.000000     2.500000
19           French Polynesia   6.333333     4.666667
49               Saudi Arabia   6.000000    10.000000
20                      Gabon   6.000000     3.000000
51                     Serbia   6.000000     3.000000
0                     Algeria   6.000000     1.000000
59                    Tunisia   5.333333     0.666667
26                  Indonesia   5.000000    12.000000
36                 Montenegro   5.000000     3.000000
65             fr:Marseille-6   5.000000     1.000000
9                      Canada   4.571429     2.857143
8                    Bulgaria   4.500000     2.000000
10                      China   4.500000     2.000000
34                 Martinique   4.500000     1.500000
62              United States   4.486653     2.921971
12             Czech Republic   4.111111     0.777778
35                     Mexico   4.000000     2.000000
2                     Andorra   4.000000     1.000000
28                    Ireland   3.666667     1.777778
17                     France   3.597405     2.436893
29                      Italy   3.578431     1.441176
21                    Germany   3.526601     1.198030
13                    Denmark   3.440000     1.680000
57                Switzerland   3.412214     2.030534
33                      Malta   3.333333     1.333333
48  Saint Pierre and Miquelon   3.333333     1.333333
44                   Portugal   3.316832     2.217822
6                     Belgium   3.284768     2.420530
38                Netherlands   3.250000     1.928571
45                    Romania   3.225000     1.925000
4                   Australia   3.090909     1.099174
39              New Caledonia   3.000000     4.333333
27                       Iraq   3.000000     3.000000
25                      India   3.000000     1.000000
58                   Thailand   3.000000     1.000000
24                    Hungary   2.833333     1.333333
61             United Kingdom   2.806653     2.126819
41                     Norway   2.777778     0.722222
40                New Zealand   2.772727     2.931818
32                 Luxembourg   2.500000     5.000000
16                    Finland   2.400000     1.000000
22                     Greece   2.333333     3.666667
23                 Guadeloupe   2.307692     3.307692
5                     Austria   2.222222     1.888889
47                    Réunion   2.111111     1.555556
43                     Poland   2.041667     1.833333
15             European Union   2.000000     2.000000
64              fr:Angleterre   2.000000     2.000000
30                      Japan   2.000000     0.250000
11                     Cyprus   2.000000     0.000000
56                     Sweden   1.906250     2.343750
55                      Spain   1.874172     1.496689
46                     Russia   1.681818     1.909091
54               South Africa   1.500000     2.666667
52                  Singapore   1.333333     3.666667
18              French Guiana   1.250000     0.000000
1                   Allemagne   1.000000     1.000000
42                       Peru   1.000000     1.000000
60       United Arab Emirates   1.000000     1.000000
7                      Brazil   1.000000     0.500000
50                   Scotland   1.000000     0.500000
3                     Armenia   1.000000     0.000000
14                    Estonia   1.000000     0.000000
31                    Lebanon   1.000000     0.000000
63                de:Scotland   1.000000     0.000000

In [9]:
import plotly.plotly as py
import plotly.graph_objs as go
py.sign_in('viveksethia', 'y0nvnlhe12')


trace1 = go.Bar(
    x=plot_data['countries_en'][:50],
    y=plot_data['allergens'],
    name='Allergens'
)
trace2 = go.Bar(
    x=plot_data['countries_en'][:50],
    y=plot_data['additives_n'],
    name='Additives'
)

data = [trace1, trace2]
layout = go.Layout(
    #xaxis=dict(tickangle=-180),
    barmode='group',
    height=700,
    margin=go.Margin(
        l=50,
        r=50,
        b=150,
        t=100,
        pad=4
    ),
)

fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='grouped-bar-1', bbox_inches='tight')

In [10]:

food

code  \
0                        0000000003087   
1                        0000000024600   
2                        0000000027083   
3                        0000000027205   
4                        0000000036252   
5                        0000000039259   
6                        0000000039529   
7                        0000000056434   
8                        0000001071894   
9                        0000001471762   
10                       0000001798180   
11                       0000003297759   
12                       0000005200016   
13                       0000007020254   
14                       0000007730009   
15                       0000009336247   
16                       0000010090206   
17                       0000010127735   
18                       0000012345878   
19                       0000020004552   
20                       0000020364373   
21                       0000024089517   
22                       0000027533024   
23                       0000027533048   
24                       0000030053014   
25                       0000040608754   
26                       0000050985098   
27                       0000054491472   
28                       0000054491496   
29                       0000069105241   
30                       0000075001629   
31                            00000758   
32                       0000080007838   
33                       0000084154071   
34                       0000087177756   
35                              000010   
36                            00001373   
37                       0000140000083   
38                            00002523   
39                            00002929   
40                            00003001   
41                              000031   
42                            00003100   
43                            00005487   
44                            00006666   
45                            00007658   
46                       0000790310013   
47                       0000790310020   
48                       0000790310044   
49                            00008433   
...                                ...   
106408                   9614241423897   
106409                   9616211004976   
106410                      9661975680   
106411                   9674192874001   
106412                   9674442897071   
106413                   9677189470408   
106414                   9680150038071   
106415                   9680150261523   
106416                   9680150808353   
106417                   9680900070818   
106418                   9685082739058   
106419                   9688014090357   
106420                   9688084817410   
106421                   9688180745372   
106422                   9688180760986   
106423                   9688180778271   
106424                   9691122630827   
106425                   9700168950216   
106426                   9700633222886   
106427                  97055722040915   
106428                   9717166772788   
106429                   9717500876868   
106430                   9752025110103   
106431  976333456799876345676542346789   
106432                   9771832875005   
106433                   9780201379129   
106434                   9782253063339   
106435                   9782266245449   
106436                   9782297003629   
106437                   9782360981342   
106438                   9787900420206   
106439                   9789604920457   
106440                   9791463741241   
106441                         9802735   
106442                   9820111458900   
106443                   9847548283004   
106444                     98709870987   
106445                      9871311007   
106446                   9876567898765   
106447                          989898   
106448                   9900010011557   
106449                   9901198001583   
106450                        99044169   
106451                   9906410000009   
10

In [11]:
## Andi ##

# get a list of all candy tags and combinations of candy tags, get all foods who's tags are in that list.
# bad approach because it's slow and if something contains candy tags + non-candy tags (e.g. 'desserts, water')
# it falls through the cracks. Sadly I can't figure out how to do
# "for candy_tag in candy_tags: get items where candy_tag in food['categories_tags']"

from itertools import combinations

candy_tags = ["en:sugary-snacks", "en:desserts", "en:candies", "en:chocolates", "en:pies", "en:puddings", 
 "en:biscuits-and-cakes", "en:confectioneries", "en:chocolate-chip-cookies", "en:chocolate-block", 
 "en:jelly-crystals", "en:carrot-cake", "en:chocolate-covered-muesli-bar"]
augmented_tags = candy_tags

for i in range(2, 4):
    augmented_tags += [",".join(map(str, comb)) for comb in combinations(candy_tags, i)]

#augmented_tags
tagged_candies = food[food['categories_tags'].isin(augmented_tags)]

#tagged_candies = [item for item in food if not set(augmented_tags).isdisjoint(item['categories_tags'])]
                           
tagged_candies

code                                                url  \
193     0009542018085  http://world-en.openfoodfacts.org/product/0009...   
293          00116954  http://world-en.openfoodfacts.org/product/0011...   
535     0016000159105  http://world-en.openfoodfacts.org/product/0016...   
682     0018000428410  http://world-en.openfoodfacts.org/product/0018...   
781     0021000419074  http://world-en.openfoodfacts.org/product/0021...   
1266    0034000405688  http://world-en.openfoodfacts.org/product/0034...   
1268    0034000440887  http://world-en.openfoodfacts.org/product/0034...   
1274    0034000473038  http://world-en.openfoodfacts.org/product/0034...   
1346    0036778020582  http://world-en.openfoodfacts.org/product/0036...   
1354    0037014242317  http://world-en.openfoodfacts.org/product/0037...   
1365    0037466030890  http://world-en.openfoodfacts.org/product/0037...   
1370    0037466062266  http://world-en.openfoodfacts.org/product/0037...   
1445    0038817002016  http://world-en.openfoodfacts.org/product/0038...   
1747    0042444687782  http://world-en.openfoodfacts.org/product/0042...   
1768    0043000204337  http://world-en.openfoodfacts.org/product/0043...   
1769    0043000204450  http://world-en.openfoodfacts.org/product/0043...   
2481    0060383042400  http://world-en.openfoodfacts.org/product/0060...   
2515    0060383998622  http://world-en.openfoodfacts.org/product/0060...   
3991         00888707  http://world-en.openfoodfacts.org/product/0088...   
4075         00929523  http://world-en.openfoodfacts.org/product/0092...   
5663         03424607  http://world-en.openfoodfacts.org/product/0342...   
5998    0628915168358  http://world-en.openfoodfacts.org/product/0628...   
6045    0639277515353  http://world-en.openfoodfacts.org/product/0639...   
6234    0708656100005  http://world-en.openfoodfacts.org/product/0708...   
6456    0747599700743  http://world-en.openfoodfacts.org/product/0747...   
6517    0762210162489  http://world-en.openfoodfacts.org/product/0762...   
6648    0799439187078  http://world-en.openfoodfacts.org/product/0799...   
6668    0810257003514  http://world-en.openfoodfacts.org/product/0810...   
7249    1048686378234  http://world-en.openfoodfacts.org/product/1048...   
7585         14151897  http://world-en.openfoodfacts.org/product/1415...   
7696         16939545  http://world-en.openfoodfacts.org/product/1693...   
7869    2000000002246  http://world-en.openfoodfacts.org/product/2000...   
7984    2000000006852  http://world-en.openfoodfacts.org/product/2000...   
8466    2000000023565  http://world-en.openfoodfacts.org/product/2000...   
8468    2000000023650  http://world-en.openfoodfacts.org/product/2000...   
8520    2000000024964  http://world-en.openfoodfacts.org/product/2000...   
8546    2000000025586  http://world-en.openfoodfacts.org/product/2000...   
8547    2000000025587  http://world-en.openfoodfacts.org/product/2000...   
8572    2000000026816  http://world-en.openfoodfacts.org/product/2000...   
8604    2000000028365  http://world-en.openfoodfacts.org/product/2000...   
9328         20012274  http://world-en.openfoodfacts.org/product/2001...   
9687         20056629  http://world-en.openfoodfacts.org/product/2005...   
9795         20073268  http://world-en.openfoodfacts.org/product/2007...   
9850         20084349  http://world-en.openfoodfacts.org/product/2008...   
9851         20084790  http://world-en.openfoodfacts.org/product/2008...   
9877         20091187  http://world-en.openfoodfacts.org/product/2009...   
10090        20128029  http://world-en.openfoodfacts.org/product/2012...   
10407        20187002  http://world-en.openfoodfacts.org/product/2018...   
10579        20229551  http://world-en.openfoodfacts.org/product/2022...   
11483   2044318097336  http://world-en.openfoodfacts.org/product/2044...   
...               ...                                                ...   
94602   8008698005231  http://world-en.openfoodfacts.org/product/

In [12]:
food_not_tagged_as_candy = food[~food['categories_tags'].isin(augmented_tags)]

food_not_tagged_as_candy

code  \
0                        0000000003087   
1                        0000000024600   
2                        0000000027083   
3                        0000000027205   
4                        0000000036252   
5                        0000000039259   
6                        0000000039529   
7                        0000000056434   
8                        0000001071894   
9                        0000001471762   
10                       0000001798180   
11                       0000003297759   
12                       0000005200016   
13                       0000007020254   
14                       0000007730009   
15                       0000009336247   
16                       0000010090206   
17                       0000010127735   
18                       0000012345878   
19                       0000020004552   
20                       0000020364373   
21                       0000024089517   
22                       0000027533024   
23                       0000027533048   
24                       0000030053014   
25                       0000040608754   
26                       0000050985098   
27                       0000054491472   
28                       0000054491496   
29                       0000069105241   
30                       0000075001629   
31                            00000758   
32                       0000080007838   
33                       0000084154071   
34                       0000087177756   
35                              000010   
36                            00001373   
37                       0000140000083   
38                            00002523   
39                            00002929   
40                            00003001   
41                              000031   
42                            00003100   
43                            00005487   
44                            00006666   
45                            00007658   
46                       0000790310013   
47                       0000790310020   
48                       0000790310044   
49                            00008433   
...                                ...   
106408                   9614241423897   
106409                   9616211004976   
106410                      9661975680   
106411                   9674192874001   
106412                   9674442897071   
106413                   9677189470408   
106414                   9680150038071   
106415                   9680150261523   
106416                   9680150808353   
106417                   9680900070818   
106418                   9685082739058   
106419                   9688014090357   
106420                   9688084817410   
106421                   9688180745372   
106422                   9688180760986   
106423                   9688180778271   
106424                   9691122630827   
106425                   9700168950216   
106426                   9700633222886   
106427                  97055722040915   
106428                   9717166772788   
106429                   9717500876868   
106430                   9752025110103   
106431  976333456799876345676542346789   
106432                   9771832875005   
106433                   9780201379129   
106434                   9782253063339   
106435                   9782266245449   
106436                   9782297003629   
106437                   9782360981342   
106438                   9787900420206   
106439                   9789604920457   
106440                   9791463741241   
106441                         9802735   
106442                   9820111458900   
106443                   9847548283004   
106444                     98709870987   
106445                      9871311007   
106446                   9876567898765   
106447                          989898   
106448                   9900010011557   
106449                   9901198001583   
106450                        99044169   
106451                   9906410000009   
10

In [13]:
candies_around_50_carbs = tagged_candies[tagged_candies['carbohydrates_100g'].astype(float) > 47]
candies_around_50_carbs = candies_around_50_carbs[candies_around_50_carbs['carbohydrates_100g'].astype(float) < 57]

candies_around_50_carbs

#candies_below = tagged_candies[tagged_candies['carbohydrates_100g'].astype(float) < 20]
#candies_below
#candies_above = tagged_candies[tagged_candies['carbohydrates_100g'].astype(float) > 65]
#candies_above

code                                                url  \
193     0009542018085  http://world-en.openfoodfacts.org/product/0009...   
1268    0034000440887  http://world-en.openfoodfacts.org/product/0034...   
1346    0036778020582  http://world-en.openfoodfacts.org/product/0036...   
1370    0037466062266  http://world-en.openfoodfacts.org/product/0037...   
2515    0060383998622  http://world-en.openfoodfacts.org/product/0060...   
5998    0628915168358  http://world-en.openfoodfacts.org/product/0628...   
8604    2000000028365  http://world-en.openfoodfacts.org/product/2000...   
9851         20084790  http://world-en.openfoodfacts.org/product/2008...   
10407        20187002  http://world-en.openfoodfacts.org/product/2018...   
13186        22145819  http://world-en.openfoodfacts.org/product/2214...   
13195        22147172  http://world-en.openfoodfacts.org/product/2214...   
13480        23048034  http://world-en.openfoodfacts.org/product/2304...   
14733        26039831  http://world-en.openfoodfacts.org/product/2603...   
15607        27039588  http://world-en.openfoodfacts.org/product/2703...   
15979        29035304  http://world-en.openfoodfacts.org/product/2903...   
16031        29047895  http://world-en.openfoodfacts.org/product/2904...   
19554   3046920000437  http://world-en.openfoodfacts.org/product/3046...   
19619   3046920017503  http://world-en.openfoodfacts.org/product/3046...   
19629   3046920020138  http://world-en.openfoodfacts.org/product/3046...   
19716   3046920045766  http://world-en.openfoodfacts.org/product/3046...   
19719   3046920047128  http://world-en.openfoodfacts.org/product/3046...   
20383   3069942320901  http://world-en.openfoodfacts.org/product/3069...   
20384   3069942320956  http://world-en.openfoodfacts.org/product/3069...   
22030   3110844197143  http://world-en.openfoodfacts.org/product/3110...   
25042   3178530404630  http://world-en.openfoodfacts.org/product/3178...   
29638   3245390589309  http://world-en.openfoodfacts.org/product/3245...   
29719   3245411868130  http://world-en.openfoodfacts.org/product/3245...   
34457   3256220509435  http://world-en.openfoodfacts.org/product/3256...   
34485   3256220610704  http://world-en.openfoodfacts.org/product/3256...   
51227   3421370012627  http://world-en.openfoodfacts.org/product/3421...   
55096   3545360006844  http://world-en.openfoodfacts.org/product/3545...   
57433   3560070899524  http://world-en.openfoodfacts.org/product/3560...   
62706   3596710410828  http://world-en.openfoodfacts.org/product/3596...   
68881   4000161060710  http://world-en.openfoodfacts.org/product/4000...   
69054   4000417012005  http://world-en.openfoodfacts.org/product/4000...   
69056   4000417015006  http://world-en.openfoodfacts.org/product/4000...   
69058   4000417017000  http://world-en.openfoodfacts.org/product/4000...   
69070   4000417044303  http://world-en.openfoodfacts.org/product/4000...   
69076   4000417210005  http://world-en.openfoodfacts.org/product/4000...   
69077   4000417211002  http://world-en.openfoodfacts.org/product/4000...   
69081   4000417222008  http://world-en.openfoodfacts.org/product/4000...   
69084   4000417236005  http://world-en.openfoodfacts.org/product/4000...   
69087   4000417269003  http://world-en.openfoodfacts.org/product/4000...   
69089   4000417280008  http://world-en.openfoodfacts.org/product/4000...   
69090   4000417289001  http://world-en.openfoodfacts.org/product/4000...   
69093   4000417298003  http://world-en.openfoodfacts.org/product/4000...   
69095   4000417304001  http://world-en.openfoodfacts.org/product/4000...   
69096   4000417305008  http://world-en.openfoodfacts.org/product/4000...   
69097   4000417413109  http://world-en.openfoodfacts.org/product/4000...   
69101   4000417601001  http://world-en.openfoodfacts.org/product/4000...   
...               ...                                                ...   
84924   5601002009012  http://world-en.openfoodfacts.org/product/

In [14]:
candies_around_50_sugar = tagged_candies[tagged_candies['sugars_100g'].astype(float) > 45]
candies_around_50_sugar = candies_around_50_carbs[candies_around_50_carbs['sugars_100g'].astype(float) < 55]

candies_around_50_sugar

#candies_below = tagged_candies[tagged_candies['sugars_100g'].astype(float) < 30]
#candies_below
candies_above = tagged_candies[tagged_candies['sugars_100g'].astype(float) > 65]
candies_above

code                                                url  \
1768    0043000204337  http://world-en.openfoodfacts.org/product/0043...   
1769    0043000204450  http://world-en.openfoodfacts.org/product/0043...   
2515    0060383998622  http://world-en.openfoodfacts.org/product/0060...   
8572    2000000026816  http://world-en.openfoodfacts.org/product/2000...   
9687         20056629  http://world-en.openfoodfacts.org/product/2005...   
14267   2600280009649  http://world-en.openfoodfacts.org/product/2600...   
14268   2600280011543  http://world-en.openfoodfacts.org/product/2600...   
14269   2600280012205  http://world-en.openfoodfacts.org/product/2600...   
15254        26172552  http://world-en.openfoodfacts.org/product/2617...   
21680   3103220006603  http://world-en.openfoodfacts.org/product/3103...   
21706   3103220009819  http://world-en.openfoodfacts.org/product/3103...   
25200   3179142053001  http://world-en.openfoodfacts.org/product/3179...   
43823   3276650400089  http://world-en.openfoodfacts.org/product/3276...   
69927   4002890002979  http://world-en.openfoodfacts.org/product/4002...   
70617   4007384000073  http://world-en.openfoodfacts.org/product/4007...   
72183   4019400440633  http://world-en.openfoodfacts.org/product/4019...   
72379   4023800051344  http://world-en.openfoodfacts.org/product/4023...   
72834   4038857117516  http://world-en.openfoodfacts.org/product/4038...   
74647   4311501306390  http://world-en.openfoodfacts.org/product/4311...   
77568   5000159471916  http://world-en.openfoodfacts.org/product/5000...   
77735   5000169122938  http://world-en.openfoodfacts.org/product/5000...   
78914   5011701000027  http://world-en.openfoodfacts.org/product/5011...   
82190   5400141193336  http://world-en.openfoodfacts.org/product/5400...   
84936   5601008600688  http://world-en.openfoodfacts.org/product/5601...   
85451   5701073062302  http://world-en.openfoodfacts.org/product/5701...   
85922   5900951141638  http://world-en.openfoodfacts.org/product/5900...   
88768   7610809115992  http://world-en.openfoodfacts.org/product/7610...   
102542  8713600281169  http://world-en.openfoodfacts.org/product/8713...   
105031  9300619501273  http://world-en.openfoodfacts.org/product/9300...   

                           creator   created_t      created_datetime  \
1768                      stephane  1441263361  2015-09-03T06:56:01Z   
1769                 aaronasachimp  1462241673  2016-05-03T02:14:33Z   
2515                   hummingbrid  1434935913  2015-06-22T01:18:33Z   
8572                       javichu  1454017614  2016-01-28T21:46:54Z   
9687    openfoodfacts-contributors  1415308593  2014-11-06T21:16:33Z   
14267                   agamitsudo  1460905382  2016-04-17T15:03:02Z   
14268                   agamitsudo  1460901488  2016-04-17T13:58:08Z   
14269                   agamitsudo  1460904632  2016-04-17T14:50:32Z   
15254                  foodorigins  1451026327  2015-12-25T06:52:07Z   
21680   openfoodfacts-contributors  1432842151  2015-05-28T19:42:31Z   
21706                         oc84  1427535009  2015-03-28T09:30:09Z   
25200                       tacite  1448388580  2015-11-24T18:09:40Z   
43823                     sebleouf  1437488190  2015-07-21T14:16:30Z   
69927                        kakao  1461655456  2016-04-26T07:24:16Z   
70617                  anticultist  1477771202  2016-10-29T20:00:02Z   
72183                       tacite  1420039871  2014-12-31T15:31:11Z   
72379                        kakao  1464252609  2016-05-26T08:50:09Z   
72834                    twoflower  1440533239  2015-08-25T20:07:19Z   
74647                        kakao  1462629711  2016-05-07T14:01:51Z   
77568                    twoflower  1447699250  2015-11-16T18:40:50Z   
77735                     bcatelin  1476464501  2016-10-14T17:01:41Z   
78914                     sebleouf  1429611734  2015-04-21T10:22:14Z   
82190                      lelutin  1448547130  2015-11-26T14:12:10Z   
84936   

In [23]:
candies_around_x_sugar = tagged_candies[tagged_candies['sugars_100g'].astype(float) > 22]
candies_around_x_sugar = candies_around_x_sugar[candies_around_x_sugar['sugars_100g'].astype(float) < 30]

candies_around_x_sugar = candies_around_x_sugar[candies_around_x_sugar['carbohydrates_100g'].astype(float) > 30]


candies_around_x_sugar

code                                                url  \
293         00116954  http://world-en.openfoodfacts.org/product/0011...   
4075        00929523  http://world-en.openfoodfacts.org/product/0092...   
7696        16939545  http://world-en.openfoodfacts.org/product/1693...   
10090       20128029  http://world-en.openfoodfacts.org/product/2012...   
28098  3226210100010  http://world-en.openfoodfacts.org/product/3226...   
31416  3250390682486  http://world-en.openfoodfacts.org/product/3250...   
31992  3250391334919  http://world-en.openfoodfacts.org/product/3250...   
47213  3340292025600  http://world-en.openfoodfacts.org/product/3340...   
51227  3421370012627  http://world-en.openfoodfacts.org/product/3421...   
61829  3596710339976  http://world-en.openfoodfacts.org/product/3596...   
64243  3661893211132  http://world-en.openfoodfacts.org/product/3661...   
64982  3700311810516  http://world-en.openfoodfacts.org/product/3700...   
66685  3760077180230  http://world-en.openfoodfacts.org/product/3760...   
66690  3760077181725  http://world-en.openfoodfacts.org/product/3760...   
68440  3770000409000  http://world-en.openfoodfacts.org/product/3770...   
69239  4000539001505  http://world-en.openfoodfacts.org/product/4000...   
70856  4008400191423  http://world-en.openfoodfacts.org/product/4008...   
70994       40084725  http://world-en.openfoodfacts.org/product/4008...   
70995       40084794  http://world-en.openfoodfacts.org/product/4008...   
72337  4021851635827  http://world-en.openfoodfacts.org/product/4021...   
73484  4101540709289  http://world-en.openfoodfacts.org/product/4101...   
73485  4101540710377  http://world-en.openfoodfacts.org/product/4101...   
78937  5011835104028  http://world-en.openfoodfacts.org/product/5011...   
80521  5054070099605  http://world-en.openfoodfacts.org/product/5054...   
81284  5099872009520  http://world-en.openfoodfacts.org/product/5099...   
83056  5410126050455  http://world-en.openfoodfacts.org/product/5410...   
84445  5425008345024  http://world-en.openfoodfacts.org/product/5425...   
84448  5425008345062  http://world-en.openfoodfacts.org/product/5425...   
84451  5425008345093  http://world-en.openfoodfacts.org/product/5425...   
84452  5425008345109  http://world-en.openfoodfacts.org/product/5425...   
84453  5425008345116  http://world-en.openfoodfacts.org/product/5425...   
88766  7610809111086  http://world-en.openfoodfacts.org/product/7610...   
88858  7610848492740  http://world-en.openfoodfacts.org/product/7610...   
91402  7622210250452  http://world-en.openfoodfacts.org/product/7622...   
93103  8000500200018  http://world-en.openfoodfacts.org/product/8000...   
94369  8006380232583  http://world-en.openfoodfacts.org/product/8006...   

                          creator   created_t      created_datetime  \
293                       tacinte  1408885358  2014-08-24T13:02:38Z   
4075   openfoodfacts-contributors  1422734299  2015-01-31T19:58:19Z   
7696                       aleene  1478333982  2016-11-05T08:19:42Z   
10090                      aleene  1462373040  2016-05-04T14:44:00Z   
28098  openfoodfacts-contributors  1461434885  2016-04-23T18:08:05Z   
31416                  tib-de-bar  1468101377  2016-07-09T21:56:17Z   
31992             date-limite-app  1462124083  2016-05-01T17:34:43Z   
47213                     clems37  1477315099  2016-10-24T13:18:19Z   
51227                  agamitsudo  1452107857  2016-01-06T19:17:37Z   
61829                    ghulak75  1468751211  2016-07-17T10:26:51Z   
64243             hommedanslalune  1443646321  2015-09-30T20:52:01Z   
64982  openfoodfacts-contributors  1379442356  2013-09-17T18:25:56Z   
66685                  agamitsudo  1425111160  2015-02-28T08:12:40Z   
66690                        thib  1429285607  2015-04-17T15:46:47Z   
68440                      bruder  1424692202  2015-02-23T11:50:02Z   
69239                   twoflower  1457961627  2016-03-14T13:20:27Z   
70856                   twoflower

In [21]:
candies_around_x_carbs = tagged_candies[tagged_candies['carbohydrates_100g'].astype(float) > 22]
candies_around_x_carbs = candies_around_x_carbs[candies_around_x_carbs['carbohydrates_100g'].astype(float) < 30]

candies_around_x_carbs

Empty DataFrame
Columns: [code, url, creator, created_t, created_datetime, last_modified_t, last_modified_datetime, product_name, generic_name, quantity, packaging, packaging_tags, brands, brands_tags, categories, categories_tags, categories_en, origins, origins_tags, manufacturing_places, manufacturing_places_tags, labels, labels_tags, labels_en, emb_codes, emb_codes_tags, first_packaging_code_geo, cities, cities_tags, purchase_places, stores, countries, countries_tags, countries_en, ingredients_text, allergens, allergens_en, traces, traces_tags, traces_en, serving_size, no_nutriments, additives_n, additives, additives_tags, additives_en, ingredients_from_palm_oil_n, ingredients_from_palm_oil, ingredients_from_palm_oil_tags, ingredients_that_may_be_from_palm_oil_n, ingredients_that_may_be_from_palm_oil, ingredients_that_may_be_from_palm_oil_tags, nutrition_grade_uk, nutrition_grade_fr, pnns_groups_1, pnns_groups_2, states, states_tags, states_en, main_category, main_category_en, image_url, image_small_url, energy_100g, energy-from-fat_100g, fat_100g, saturated-fat_100g, -butyric-acid_100g, -caproic-acid_100g, -caprylic-acid_100g, -capric-acid_100g, -lauric-acid_100g, -myristic-acid_100g, -palmitic-acid_100g, -stearic-acid_100g, -arachidic-acid_100g, -behenic-acid_100g, -lignoceric-acid_100g, -cerotic-acid_100g, -montanic-acid_100g, -melissic-acid_100g, monounsaturated-fat_100g, polyunsaturated-fat_100g, omega-3-fat_100g, -alpha-linolenic-acid_100g, -eicosapentaenoic-acid_100g, -docosahexaenoic-acid_100g, omega-6-fat_100g, -linoleic-acid_100g, -arachidonic-acid_100g, -gamma-linolenic-acid_100g, -dihomo-gamma-linolenic-acid_100g, omega-9-fat_100g, -oleic-acid_100g, -elaidic-acid_100g, -gondoic-acid_100g, -mead-acid_100g, -erucic-acid_100g, -nervonic-acid_100g, trans-fat_100g, ...]
Index: []

In [17]:
import plotly.plotly as py
import plotly.graph_objs as go
py.sign_in('Odin123', '5Ba7VLNrZsqtUXUatHiZ')

candy_sugar = tagged_candies["sugars_100g"].astype(float).mean()
others_sugar = food_not_tagged_as_candy["sugars_100g"].astype(float).mean()

candy_fat = tagged_candies["fat_100g"].astype(float).mean()
others_fat = food_not_tagged_as_candy["fat_100g"].astype(float).mean()

candy_energy = tagged_candies["energy_100g"].astype(float).mean() / 1000
others_energy = food_not_tagged_as_candy["energy_100g"].astype(float).mean() / 1000

candy_carbs = tagged_candies["carbohydrates_100g"].astype(float).mean()
others_carbs = food_not_tagged_as_candy["carbohydrates_100g"].astype(float).mean()

candy_salt = tagged_candies["salt_100g"].astype(float).mean()
others_salt = food_not_tagged_as_candy["salt_100g"].astype(float).mean()

candy_nutrition_score = tagged_candies["nutrition-score-fr_100g"].astype(float).mean()
others_nutrition_score = food_not_tagged_as_candy["nutrition-score-fr_100g"].astype(float).mean()

x_names = ["sugar", "fat", "energy (MJ)", "carbohydrates", "salt", "nutrition score"]
y_values_candy = [candy_sugar, candy_fat, candy_energy, candy_carbs, candy_salt, candy_nutrition_score]
y_values_others = [others_sugar, others_fat, others_energy, others_carbs, others_salt, others_nutrition_score]

trace1 = go.Bar(
    x=x_names,
    y=y_values_candy,
    name='Candy'
)
trace2 = go.Bar(
    x=x_names,
    y=y_values_others,
    name='Other Foods'
)

data = [trace1, trace2]
layout = go.Layout(
    #xaxis=dict(tickangle=-180),
    barmode='group',
    height=700,
    margin=go.Margin(
        l=50,
        r=50,
        b=150,
        t=100,
        pad=4
    ),
)

fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='candy_others_comparison_bars', bbox_inches='tight')

PlotlyError: Hey there! You've hit one of our API request limits. 

To get unlimited API calls(10,000/day), please upgrade to a paid plan. 

UPGRADE HERE: https://goo.gl/i7glmM 

Thanks for using Plotly! Happy Plotting!

In [ ]:
trace1 = go.Histogram(
    x=tagged_candies["salt_100g"].astype(float),
)

layout = go.Layout(
    title='Salt (in g) in Candy',
    xaxis=dict(
        title='salt in 100g (steps of 5)'
    ),
    yaxis=dict(
        title='Number of candy in interval'
    ),
    bargap=0.01
)
data = [trace1]

fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='candy_salt_histo')

In [ ]:
trace1 = go.Histogram(
    x=tagged_candies["sugars_100g"].astype(float),
)

layout = go.Layout(
    title='Sugar (in g) in Candy',
    xaxis=dict(
        title='sugar in 100g (steps of 5)'
    ),
    yaxis=dict(
        title='Number of candy in interval'
    ),
    bargap=0.01
)
data = [trace1]

fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='candy_sugar_histo')

In [ ]:
trace1 = go.Histogram(
    x=tagged_candies["fat_100g"].astype(float),
)

layout = go.Layout(
    title='Fat (in g) in Candy',
    xaxis=dict(
        title='fat in 100g (steps of 5)'
    ),
    yaxis=dict(
        title='Number of candy in interval'
    ),
    bargap=0.01
)
data = [trace1]

fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='candy_fat_histo')

In [ ]:
trace1 = go.Histogram(
    x=tagged_candies["carbohydrates_100g"].astype(float),
)

layout = go.Layout(
    title='Carbohydrates (in g) in Candy',
    xaxis=dict(
        title='carbohydrates in 100g (steps of 5)'
    ),
    yaxis=dict(
        title='Number of candy in interval'
    ),
    bargap=0.01
)
data = [trace1]

fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='candy_carbs_histo')

In [ ]:
trace1 = go.Histogram(
    x=food_not_tagged_as_candy["carbohydrates_100g"].astype(float),
)

layout = go.Layout(
    title='Carbohydrates in Others',
    xaxis=dict(
        title='carbohydrates in 100g'
    ),
    yaxis=dict(
        title='Number of items in interval'
    ),
    bargap=0.01
)
data = [trace1]

fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='others_carbs_histo')